In [1]:
import py_trees
import behaviours as be
from py_trees.blackboard import Blackboard
import pandas as pd
from scipy import spatial
from sklearn.cluster import KMeans
import numpy as np
from pandas import DataFrame
from annotator import annotator
import re

In [15]:
docu = '/Users/sileshu/Desktop/EMSdata/RAA Data 2017.xlsx'
df = pd.read_excel(docu)
narratives = df['Narrative']
interventions = df['Interventions']

In [4]:
docu = '/Users/sileshu/Desktop/BT/AutoLabelCases (Haydon Additions).xlsx'
df = pd.read_excel(docu)
su = 0
protocol = {}
narratives = df['Narratives']
gt = []
pts = set()
for item in df['Corrected Protocol']:
    if not pd.isnull(item):
        gt.append(item)
        pts.add(item)
        
for item in df.iterrows():
    if item[1]['Corrected Protocol'] in protocol:
        protocol[item[1]['Corrected Protocol']] += 1
    else:
        protocol[item[1]['Corrected Protocol']] = 1


KeyError: 'Narratives'

In [9]:
res = []
for item in df.iterrows():
    inter = item[1]['Interventions'].strip('{}').split('}{')
    inter = [i.split(':')[-1].strip().lower() for i in inter]
    if len(inter) <= 2 and 'hospital contact' in inter:
        continue
    impression = item[1]['Impressions'].strip('{}').split('}{')
    chief_complain = item[1]['CheifComplaint'].strip('{}').split('}{')
    cc = []
    for i in chief_complain:
        temp = i.split('-')
        temp = [i.strip() for i in temp]
        if temp[0] == 'Cardiac':
            cc.append(temp[1])
        else:
            cc.append(temp[0])
    res.append(annotator(cc[-1],item[1]['CallType'],inter,impression))

KeyError: 'Interventions'

In [5]:
df['prediciton_1'] = res

In [6]:
df.to_excel(docu,index = False)

In [18]:
su

0

In [10]:
protocol

{u'General - Behavioral/Patient Restraint': 6,
 u'General - Cardiac Arrest': 2,
 u'General - Pain Control': 2,
 u'General - Universal Patient Care/Initial Patient Contact': 28,
 u'Injury - General Trauma Management': 9,
 u'Injury - Head': 7,
 u'Injury - Thoracic': 2,
 u'Medical - Abdominal Pain': 5,
 u'Medical - Altered Mental Status': 15,
 u'Medical - Bradycardia': 1,
 u'Medical - Chest Pain - Cardiac Suspected': 13,
 u'Medical - Diabetic - Hyperglycemia': 4,
 u'Medical - Diabetic - Hypoglycemia': 5,
 u'Medical - Hypotension/Shock': 1,
 u'Medical - Hypotension/Shock (Non-trauma)': 3,
 u'Medical - Nausea/Vomiting': 7,
 u'Medical - Overdose/Poisoning - Opioid': 13,
 u'Medical - Pulmonary Edema/CHF': 3,
 u'Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway': 4,
 u'Medical - Seizure': 4,
 u'Medical - Sepsis': 5,
 u'Medical - Stroke/TIA': 5,
 u'Medical - Supraventricular Tachycardia (including atrial\nfibrillation)': 1,
 u'Medical - Tachycardia': 1,
 u'OB/GYN - Childbirth/Lab

In [21]:
sum(protocol.values())

148

In [19]:
from search_term import search_term

In [23]:
pro_df = pd.read_excel('/Users/sileshu/Desktop/BT/ODEMSA_Protocols.xlsx')

In [24]:
ss = set()
inter = set()
for item in pro_df['Signs&Symptoms']:
    for i in item.split(';'):
        i = i.strip().lower()
        ss.add(i)
for item in pro_df['Interventions']:
    for i in item.split(';'):
        i = i.strip().lower()
        inter.add(i)

In [26]:
dft = pd.DataFrame()
dft['Required Concepts'] = list(ss)
dft.to_csv('RC.csv',index = False)

In [29]:
concept_mapping = {}
for i in ss:
    cuis = search_term(i, page_limit = 1, check = True)
    if len(cuis) == 0:
        print i
    else:
        concept_mapping[i] = cuis

In [11]:
for i in inter:
    cuis = search_term(i, page_limit = 1, check = True)
    if len(cuis) == 0:
        print i
    else:
        concept_mapping[i] = cuis

In [30]:
dfs = []
for i in concept_mapping:
    df = DataFrame()
    cuis = [j[0] for j in concept_mapping[i]]
    names = [j[1] for j in concept_mapping[i]]
    concept = [i] + [np.nan] * (len(cuis) - 1)
    df['Required Concept'] = concept
    df['CUI'] = cuis
    df['Preferred Name'] = names
    dfs.append(df)
concept_list = pd.concat(dfs)

In [31]:
concept_list.to_csv('concept_list(s&s).csv',index = False)

In [49]:
pv = {}
for line in pro_df.iterrows():
    sv = []
    iv = []
    line_ss = [i.strip().lower() for i in line[1]['Signs&Symptoms'].split(';')]
    line_inter = [i.strip().lower() for i in line[1]['Interventions'].split(';')]
    print line_ss
    name = line[1]['Protocol']
    for i in ss:
        sv.append(int(i in line_ss))
    for j in inter:
        iv.append(int(j in line_inter))
    pv[name] = sv
            

[u'chest pain', u'pain region', u'pain radiation', u'pale', u'diaphoresis', u'shortness of breath', u'nausea', u'vomiting', u'dizziness']
[u'pain', u'distension', u'rigidity', u'unequal femoral pulses', u'absent femoral pulses', u'diaphoresis', u'tenderness', u'nausea', u'vomiting', u'diarrhea', u'dysuria', u'constipation', u'vaginal bleeding', u'vaginal discharge', u'pregnancy', u'fever', u'headache', u'weakness', u'malaise', u'myalgias', u'cough', u'rash']
[u'anxiety', u'agitation', u'confusion', u'hallucinations', u'delusional thoughts', u'bizarre behavior', u'combative', u'violent', u'suicidal thought', u'homicidal thoughts']
[u'pain severity', u'pain quality', u'pain radiation', u'breath']
[u'decreased mental status', u'sleepiness', u'incontinence', u'seizure', u'trauma']
[u'shortness of breath', u'respiratory rate', u'use of accessory muscles', u'tripoding', u'wheezing', u'rhonchi', u'rales', u'fever', u'cough', u'tachycardia']
[u'loss of consciousness', u'lightheadedness', u'diz

In [50]:
l = []
names = []
for i in pv:
    names.append(i)
    l.append(pv[i])
X = np.array(l)
kmeans = KMeans(n_clusters=6, random_state=0).fit(X)

In [55]:
kmeans.labels_

[3, 2, 2, 2, 4, 0, 5, 1, 2]

In [26]:
names

[u'Diabetic/Hypoglycemia',
 u'Abdominal Pain',
 u'Respiratory Distress/Asthma/COPD/Croup/Reactive Airway',
 u'Pain Control',
 u'Altered Mental Status',
 u'Seizure',
 u'Overdose/Poisoning(Opioid)',
 u'Chest Pain',
 u'Behavioral/Patient Restraint']

In [60]:
group = dict()
for i,name in enumerate(names):
    if x[i] in group:
        group[x[i]].append(name)
    else:
        group[x[i]] = [name]

In [61]:
group

{0: [u'General - Behavioral/Patient Restraint'],
 1: [u'Medical - Diabetic - Hypoglycemia'],
 2: [u'General - Pain Control',
  u'Medical - Altered Mental Status',
  u'Medical - Seizure',
  u'Medical - Chest Pain - Cardiac Suspected'],
 3: [u'Medical - Abdominal Pain'],
 4: [u'Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway'],
 5: [u'Medical - Overdose/Poisoning - Opioid']}

In [5]:
from ranking_func import rank
def pre_tick_handler(behaviour_tree):
    blackboard = Blackboard()
    blackboard.tick_num += 1
texts = ['Upper lobes bilaterally and quiet lower lobes bilaterally initial Vital Signs BP 162 over 94 pulse 120 for respirations 36 skin is warm and moistpulse oximetry 92% on 15 LPM by non-rebreather ECG']
results = []
scores = []
ConceptRes = []
for item in narratives:
    blackboard = Blackboard()
    blackboard.text = [item]
    root = py_trees.composites.Sequence("Root_1")
    IG = be.InformationGathering()
    TC = be.TextCollection()
    V = be.Vectorize()
    root.add_children([TC,IG,V])
    behaviour_tree = py_trees.trees.BehaviourTree(root)
    behaviour_tree.add_pre_tick_handler(pre_tick_handler)
    behaviour_tree.setup(15)
    behaviour_tree.tick_tock(
            sleep_ms=50,
            number_of_iterations=1,
            pre_tick_handler=None,
       post_tick_handler=None
        )
    scores.append(blackboard.ranking)
    ConceptRes.append(blackboard.ConcLog)
    results.append(rank(blackboard.ranking))

(blood pressure,True,htn,htn,11.49,1)
(hypertension,True,htn,htn,11.49,1)
22.98
Medical - Abdominal Pain 0.0
General - Pain Control 0.0
Medical - Altered Mental Status 0.267261241912
Medical - Seizure 0.0
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.0
General - Behavioral/Patient Restraint 0.0
Medical - Overdose/Poisoning - Opioid 0.235702260396
Medical - Diabetic - Hypoglycemia 0.188982236505
Medical - Chest Pain - Cardiac Suspected 0.0
(pulse rate,True,pulse,pulse,16.3,1)
(vaginal bleeding,True,200,vaginal bleeding,3.75,1)
(lightheadedness,True,dizziness,dizziness,17.8,1)
(breath,False,dyspnea,dyspnea,14.64,1)
(trauma,False,trauma,trauma,5.18,1)
(pain,True,tx,tx,13.08,1)
(vomiting,False,vomiting,vomiting,14.64,1)
(chest pain,False,chest pain,chest pain,17.8,1)
(nausea,False,nausea,nausea,14.64,1)
(shortness of breath,False,dyspnea,dyspnea,14.64,1)
(dizziness,True,dizziness,dizziness,17.8,1)
150.27
Medical - Abdominal Pain 0.205632732889
General - Pain Control 0.

/Users/sileshu/anaconda/lib/python2.7/site-packages/scipy/spatial/distance.py:644: RuntimeWarning: invalid value encountered in double_scalars
  dist = 1.0 - uv / np.sqrt(uu * vv)


(pulse rate,True,radial pulses,radial pulses,3.54,1)
(hypotension,True,hypotension,hypotension,6.66,1)
(pregnancy,False,possibility pregnancy,possibility pregnancy,2.48,1)
(pale,True,pale color,pale color,8.98,1)
(blood pressure,True,hypotension,hypotension,6.66,1)
(lightheadedness,True,dizziness,dizziness,12.17,1)
(diarrhea,True,diarrhea,diarrhea,18.22,1)
(breath,True,lung sounds,lung sounds,8.97,1)
(trauma,False,trauma extremities upper,trauma extremities upper,4.5,1)
(wheezing,True,lung sounds,lung sounds,8.97,1)
(respiratory rate,True,breathing rate,breathing rate,11.01,1)
(headache,False,head pain,head pain,12.17,1)
(pain region,True,neck pain,neck pain,11.21,1)
(vomiting,True,nausea/vomiting,nausea/vomiting,3.54,1)
(chest pain,False,chest pain,chest pain,12.17,1)
(loss of consciousness,False,loss of consciousness,loss of consciousness,14.32,1)
(nausea,True,nausea/vomiting,nausea/vomiting,3.54,1)
(shortness of breath,True,shortness of breath,shortness of breath,3.54,1)
(malaise,Tr

(rales,True,4.,rales,13.07,1)
(rhonchi,True,4.,rales,13.07,1)
(breath,True,breath,breath,3.44,1)
(trauma,False,trauma,trauma,6.9,1)
(wheezing,True,4.,wheezing,13.07,1)
(nausea,True,feeling sick,feeling sick,13.04,1)
(shortness of breath,True,difficulty breathing,difficulty breathing,13.0,1)
75.59
Medical - Abdominal Pain 0.0921120867239
General - Pain Control 0.0569873965623
Medical - Altered Mental Status 0.0
Medical - Seizure 0.10223849753
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.547021080759
General - Behavioral/Patient Restraint 0.0
Medical - Overdose/Poisoning - Opioid 0.0
Medical - Diabetic - Hypoglycemia 0.0
Medical - Chest Pain - Cardiac Suspected 0.287587559396
(pulse rate,True,pulse,pulse,16.3,1)
(lightheadedness,False,dizziness,dizziness,17.8,1)
(diarrhea,False,diarrhea,diarrhea,14.64,1)
(breath,True,breath sounds,breath sounds,12.91,1)
(trauma,False,trauma,trauma,5.18,1)
(wheezing,True,breath sounds,breath sounds,12.91,1)
(fever,False,fever,fever,5

(breath,False,sob,sob,14.64,1)
(trauma,False,traumatic injury,traumatic injury,5.18,1)
(vomiting,True,vomiting,vomiting,29.46,1)
(loss of consciousness,False,syncope,syncope,24.11,1)
(nausea,True,nausea,nausea,13.05,1)
(shortness of breath,False,sob,sob,14.64,1)
(dizziness,False,vertigo,vertigo,17.8,1)
118.88
Medical - Abdominal Pain 0.185317194893
General - Pain Control 0.149674230574
Medical - Altered Mental Status 0.323895261188
Medical - Seizure 0.0473675269385
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.0946622951295
General - Behavioral/Patient Restraint 0.0
Medical - Overdose/Poisoning - Opioid 0.0
Medical - Diabetic - Hypoglycemia 0.0972729165671
Medical - Chest Pain - Cardiac Suspected 0.510841693148
(tripoding,True,tripoding,tripoding,3.54,1)
(blood pressure,True,htn,htn,7.85,1)
(breath,True,breath,breath,2.44,1)
(trauma,True,trauma,trauma,2.44,1)
(wheezing,True,10,wheezing,8.82,1)
(chest pain,False,chest pain,chest pain,11.14,1)
(hypertension,True,htn,

...

(diarrhea,False,118,diarrhea,14.64,1)
(trauma,True,7,trauma,3.43,1)
(vomiting,False,vomiting,vomiting,14.64,1)
(chest pain,False,chest pain,chest pain,16.08,1)
(nausea,False,nausea,nausea,14.64,1)
(shortness of breath,True,shortness of breath,shortness of breath,5.18,1)
(tenderness,False,tenderness,tenderness,3.44,1)
72.05
Medical - Abdominal Pain 0.327254064852
General - Pain Control 0.0
Medical - Altered Mental Status 0.0
Medical - Seizure 0.0497157292542
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.0530902115767
General - Behavioral/Patient Restraint 0.0
Medical - Overdose/Poisoning - Opioid 0.0
Medical - Diabetic - Hypoglycemia 0.0
Medical - Chest Pain - Cardiac Suspected 0.546007589238
(pulse rate,True,radial pulses,radial pulses,4.35,1)
(distension,True,abdomen distended,abdomen distended,2.22,1)
(diarrhea,False,diarrhea,diarrhea,8.64,1)
(breath,True,respiratory rate,respiratory rate,10.5,1)
(trauma,False,trauma,trauma,4.25,1)
(tachycardia,True,tachycardic,t

(lightheadedness,False,lightheaded,lightheaded,7.97,1)
(breath,True,decreased respiratory rate,decreased respiratory rate,2.32,1)
(confusion,True,13,confused,2.32,1)
(respiratory rate,True,decreased respiratory rate,decreased respiratory rate,2.32,1)
(fever,False,fever,fever,1.55,1)
(shortness of breath,False,sob,sob,6.55,1)
(dizziness,False,dizzy,dizzy,7.97,1)
31.0
Medical - Abdominal Pain 0.0240697507172
General - Pain Control 0.0844907614158
Medical - Altered Mental Status 0.438824161583
Medical - Seizure 0.0
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.240004261813
General - Behavioral/Patient Restraint 0.0534366494632
Medical - Overdose/Poisoning - Opioid 0.0563271742772
Medical - Diabetic - Hypoglycemia 0.200309981854
Medical - Chest Pain - Cardiac Suspected 0.352530418321
(trauma,True,head injury,head injury,6.22,1)
(loss of consciousness,True,unconscious,unconscious,10.41,1)
16.63
Medical - Abdominal Pain 0.0
General - Pain Control 0.0
Medical - Altered Me

(pulse rate,True,radial pulses,radial pulses,1.19,1)
(rales,False,2,rales,4.24,1)
(rhonchi,False,rhonchi/wheezing,rhonchi/wheezing,4.21,1)
(diarrhea,False,diarrhea,diarrhea,4.75,1)
(breath,True,shallow respirations,shallow respirations,1.12,1)
(trauma,True,spinal cord injury,spinal cord injury,4.2,1)
(wheezing,False,rhonchi/wheezing,rhonchi/wheezing,4.21,1)
(respiratory rate,True,tachypneic,tachypneic,4.22,1)
(weakness,False,weakness,weakness,1.18,1)
(vomiting,False,vomiting,vomiting,4.75,1)
(chest pain,False,chest pain,chest pain,5.24,1)
(nausea,True,nausea,nausea,17.18,1)
(shortness of breath,True,of shortness breath,of shortness breath,2.36,1)
(malaise,False,discomfort,discomfort,2.37,1)
61.22
Medical - Abdominal Pain 0.296702270233
General - Pain Control 0.0257799511212
Medical - Altered Mental Status 0.0207057994844
Medical - Seizure 0.0864685847455
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.280090984634
General - Behavioral/Patient Restraint 0.0
Medical - 

(rhonchi,True,rhonchi,rhonchi,18.07,1)
(distension,False,distended abdomen,distended abdomen,3.54,1)
(breath,True,breathing treatment,breathing treatment,9.17,1)
(wheezing,True,expiratory wheezing,expiratory wheezing,2.57,1)
(chest pain,False,chest pain,chest pain,11.04,1)
(anxiety,True,tx,tx,6.74,1)
51.13
Medical - Abdominal Pain 0.0308875253718
General - Pain Control 0.187642207508
Medical - Altered Mental Status 0.0
Medical - Seizure 0.0
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.267116605128
General - Behavioral/Patient Restraint 0.0872270309381
Medical - Overdose/Poisoning - Opioid 0.0
Medical - Diabetic - Hypoglycemia 0.0737202963246
Medical - Chest Pain - Cardiac Suspected 0.150604868839
(blood pressure,True,2/2,htn,11.49,1)
(pain region,True,neck pain,neck pain,16.26,1)
(weakness,True,weakness,weakness,3.43,1)
(diaphoresis,True,diaphoresis,diaphoresis,3.61,1)
(hypertension,True,2,htn,11.49,1)
46.28
Medical - Abdominal Pain 0.0638131963332
General - Pain 

(lightheadedness,False,dizziness,dizziness,11.58,1)
(breath,True,breath,breath,2.57,1)
(trauma,False,trauma,trauma,4.97,1)
(chest pain,True,chest pain,chest pain,35.24,1)
(dizziness,False,dizziness,dizziness,11.58,1)
65.94
Medical - Abdominal Pain 0.0
General - Pain Control 0.0327304232085
Medical - Altered Mental Status 0.222965684522
Medical - Seizure 0.0566134836725
Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway 0.0
General - Behavioral/Patient Restraint 0.0
Medical - Overdose/Poisoning - Opioid 0.0
Medical - Diabetic - Hypoglycemia 0.0788302737487
Medical - Chest Pain - Cardiac Suspected 0.397519692509
(blood pressure,True,hypertensions,hypertensions,6.68,1)
(breath,True,breath,breath,2.32,1)
(tachycardia,True,svt,svt,21.0,1)
(chest pain,True,chest pain,chest pain,10.63,1)
(hypertension,True,hypertensions,hypertensions,6.68,1)
(nausea,True,nauseous,nauseous,9.51,1)
(shortness of breath,False,difficulty breathing,difficulty breathing,8.58,1)
65.4
Medical - Abdomina

In [20]:
Inters = []
for item in interventions:
    inter = item.strip('{}').split('}{')
    inter = [i.split(':')[-1].strip().lower() for i in inter]
    Inters.append(inter)
interset = set()
for i in Inters:
    for j in i:
        interset.add(j)

In [29]:
interset

{u'1,000',
 u'10,000',
 u'12-lead ecg',
 u'acetaminophen (tylenol)',
 u'adenosine (adenocard)',
 u'aed',
 u'albuterol',
 u'alteplase (activase)',
 u'amiodarone (bolus)',
 u'amiodarone (drip)',
 u'antibiotics',
 u'aspirin',
 u'assist ventilation (bvm)',
 u'atropine',
 u'bleeding controlled',
 u'blood',
 u'burn sheet',
 u'calcium chloride',
 u'capnography (1) first reading',
 u'capnography (2) second reading',
 u'capnography (3) final reading',
 u'cardiac monitor',
 u'chest decompression',
 u'cold pack',
 u'confirm time',
 u'cpap',
 u'cpr',
 u'cricothyrotomy',
 u'cyanokit 5g',
 u'defibrillation',
 u'dexamethasone (decadron)',
 u'dextrose 10%',
 u'dextrose 25%',
 u'dextrose 5% in 0.45% ns',
 u'dextrose 50%',
 u'diazepam (valium)',
 u'diltiazem (cardizem)',
 u'diphenhydramine (benadryl)',
 u'dobutamine',
 u'dopamine',
 u'duoneb',
 u'endotracheal',
 u'enoxaparin',
 u'epi-pen (adult)',
 u'fentanyl',
 u'furosemide (lasix)',
 u'glucagon',
 u'glutose',
 u'heparin',
 u'hospital contact',
 u'hydr

In [ ]:
protocol2inter = {
    'Medical - Chest Pain - Cardiac Suspected':['oxygen','cardiac monitor','12-lead ecg',\
                               'aspirin','midazolam (versed)','diazepam (valium)',\
                                'nitroglycerine','fentanyl','hospital contact','iv','normal saline'],
    'Medical - Abdominal Pain':['oxygen','cardiac monitor','12-lead ecg',\
                                'iv','normal saline','ondansetron (zofran)','hospital contact']
    'General - Behavioral/Patient Restraint':['oxygen','midazolam (versed)','diazepam (valium)',\
                                              'hospital contact']
    'General - Pain Control':['oxygen','cardiac monitor','12-lead ecg',\
                              'acetaminophen (tylenol)','iv','normal saline','fentanyl']
    'Medical - Seizure':[]

In [22]:
len(interset)

100

In [17]:
dfr = DataFrame()
dfr['Narratives'] = narratives
dfr['Concepts'] = ['\n'.join(['(' + ','.join(i.strip('()').split(',')[:3]) + ')' for i in item]) for item in ConceptRes]
dfr.to_excel('ConceptExtracEval_ODEMSA.xlsx',index = False)


In [5]:
for i in range(len(narratives)):
    if not isinstance(narratives[i], basestring):
        print i

In [5]:
gt = df['Corrected Protocol']

In [6]:
pool = set(['Medical - Abdominal Pain',
            'General - Pain Control',
            'Medical - Altered Mental Status',
            'Medical - Seizure',
            'Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway',
            'General - Behavioral/Patient Restraint',
            'Medical - Overdose/Poisoning - Opioid',
            'Medical - Diabetic - Hypoglycemia',
            'Medical - Chest Pain - Cardiac Suspected'])

In [65]:
def rank(scores):
    srt = sorted(scores,key=lambda x: x[1], reverse=True)
    return [i[0] for i in srt]
bina = []
ranks = []
ndcgs = []

def nDCG(rank,gt,group,num):
    from numpy import log2
    for i in group:
        if gt in group[i]:
            break
    ct = len(group[i]) - 1
    idcg = 2.
    idx = 1
    num -= 1
    while (ct&num):
        idcg += 1/log2(idx+2)
        idx += 1
        ct -= 1
        num -= 1
    
    dcg = 0.
    for idx,item in enumerate(rank):
        if item == gt:
            dcg += 2/log2(idx+2)
        elif item in group[i]:
            dcg += 1/log2(idx+2)
        else:
            continue
    return dcg/idcg

for i,s in enumerate(rankings):
    res = rank(s)
    
    if gt[i] in pool:
        bina.append(gt[i] in res[:3])
        ranks.append(res)
        ndcgs.append(nDCG(res[:3],gt[i],group,3))


In [66]:
float(sum(bina))/len(bina)

0.5522388059701493

In [67]:
float(sum(ndcgs)/len(ndcgs))

0.5044319125195492

In [19]:
t = [i[1]['Narratives'] for i in df.iterrows() if i[1]['Corrected Protocol'] in pool]

In [20]:
len(t)

67

In [24]:
len(ranks)

67

In [25]:
dfr = DataFrame()
dfr['Narratives'] = t
dfr['Scores'] = [s for i,s in enumerate(rankings) if gt[i] in pool]
dfr['Rank'] = ranks
dfr['GroundTruth'] = [g for g in gt if g in pool]
dfr['Correctness'] = bina

In [27]:
dfr.to_excel('VecMethEval_ODEMSA.xlsx',index = False)

In [18]:
def rank(scores):
    srt = sorted(scores,key=lambda x: x[1], reverse=True)
    return [i[0] for i in srt]

In [23]:
srt = sorted(rankings[0],key=lambda x: x[1], reverse=True)
srt

[(u'Medical - Chest Pain - Cardiac Suspected', 0.3191584088288637),
 (u'Medical - Overdose/Poisoning - Opioid', 0.31573913198725911),
 (u'Medical - Respiratory Distress/Asthma/COPD/Croup/Reactive Airway',
  0.29061596127191613),
 (u'General - Pain Control', 0.1479225788180526),
 (u'Medical - Seizure', 0.14492144015303021),
 (u'Medical - Diabetic - Hypoglycemia', 0.086607125688421882),
 (u'Medical - Abdominal Pain', 0.063074399538356141),
 (u'Medical - Altered Mental Status', 0.0),
 (u'General - Behavioral/Patient Restraint', 0.0)]

In [68]:
ndcgs

[1.0,
 1.0,
 0.0,
 0.38009376671593426,
 0.76018753343186851,
 0.0,
 0.38009376671593426,
 0.0,
 0.0,
 0.63092975357145753,
 0.0,
 0.85971869985219718,
 0.42985934992609859,
 1.0,
 0.0,
 0.95023441678983556,
 0.95023441678983556,
 0.5,
 0.95023441678983556,
 1.0,
 0.95023441678983556,
 1.0,
 0.63092975357145753,
 0.0,
 1.1900468833579672,
 0.5,
 0.61990623328406569,
 0.19004688335796713,
 0.63092975357145753,
 0.0,
 0.85971869985219718,
 0.0,
 0.0,
 0.0,
 0.76018753343186851,
 0.76018753343186851,
 0.5,
 0.63092975357145753,
 0.0,
 1.1900468833579672,
 0.0,
 0.0,
 1.0,
 0.0,
 0.57014065007390136,
 0.85971869985219718,
 0.5,
 0.38009376671593426,
 0.0,
 0.63092975357145753,
 0.38009376671593426,
 0.0,
 0.57014065007390136,
 0.0,
 0.23981246656813146,
 0.76018753343186851,
 0.85971869985219718,
 0.76018753343186851,
 1.0,
 0.63092975357145753,
 0.0,
 0.5,
 0.19004688335796713,
 1.0,
 1.1900468833579672,
 0.57014065007390136,
 0.0]